# PaperBroker Client - Complete Tutorial

**Comprehensive guide** covering all trading scenarios with a single persistent connection.

---

## 📚 Table of Contents

1. [Setup & Configuration](#1-setup--configuration)
2. [Example 1: Simple Login & Account Info](#2-example-1-simple-login--account-info)
3. [Example 2: Order Cancellation](#3-example-2-order-cancellation)
4. [Example 3: Cross-Matching Derivative](#4-example-3-cross-matching-derivative)
5. [Example 4: Advanced Cross-Matching](#5-example-4-advanced-cross-matching)
6. [Summary & Best Practices](#6-summary--best-practices)

---

## 🎯 Learning Path

- **Beginner**: Examples 1-2 (Login, Cancellation)
- **Intermediate**: Example 3 (Simple Cross-Matching)
- **Advanced**: Example 4 (Multiple Orders, FIFO)

---

**Key Feature**: This notebook uses a **single persistent connection** throughout all examples - no need to disconnect/reconnect between examples!

## 1. Setup & Configuration

### Prerequisites

1. Python 3.10+
2. PaperBroker account with FIX access
3. Required packages installed

### Import Libraries

In [1]:
import os
import sys
import time
import logging
from pathlib import Path
from threading import Event as ThreadEvent
from dotenv import load_dotenv

# Add parent directory to path
sys.path.insert(0, str(Path.cwd().parent))

from paperbroker.client import PaperBrokerClient

# Load environment variables
load_dotenv()

# Setup logging
logging.basicConfig(
    level=logging.INFO,
    format='[%(asctime)s] [%(levelname)s] %(message)s',
    datefmt='%H:%M:%S'
)
logger = logging.getLogger(__name__)

print("✅ Imports complete!")

✅ Imports complete!


### Configuration & Client Creation

**Important**: We create **ONE client** and use it for all examples. No disconnect/reconnect needed!

In [2]:
# Configuration
CONFIG = {
    "username": os.getenv("PAPER_USERNAME", "cross_fix"),
    "password": os.getenv("PAPER_PASSWORD", "123"),
    "socket_host": os.getenv("SOCKET_HOST", "100.97.83.110"),
    "socket_port": int(os.getenv("SOCKET_PORT", "5001")),
    "sender_comp_id": os.getenv("SENDER_COMP_ID", "cross-FIX"),
    "target_comp_id": os.getenv("TARGET_COMP_ID", "SERVER"),
    "rest_base_url": os.getenv("PAPER_REST_BASE_URL", "http://100.97.83.110:9090"),
    "account_d1": os.getenv("PAPER_ACCOUNT_ID_D1", "D1"),
    "account_d2": os.getenv("PAPER_ACCOUNT_ID_D2", "D2"),
    "symbol_derivative": os.getenv("VN30F1M", "HNXDS:VN30F2511"),
}

print("📝 Configuration:")
for key, value in CONFIG.items():
    if key == "password":
        print(f"  {key}: ***")
    else:
        print(f"  {key}: {value}")

print("\n" + "=" * 80)
print("🔌 CREATING PERSISTENT CLIENT")
print("=" * 80)

# Create ONE client for all examples
client = PaperBrokerClient(
    default_sub_account=CONFIG["account_d1"],
    username=CONFIG["username"],
    password=CONFIG["password"],
    rest_base_url=CONFIG["rest_base_url"],
    socket_connect_host=CONFIG["socket_host"],
    socket_connect_port=CONFIG["socket_port"],
    sender_comp_id=CONFIG["sender_comp_id"],
    target_comp_id=CONFIG["target_comp_id"],
    console=False,
)

# Connect
logger.info("🔌 Connecting to PaperBroker...")
client.connect()

# Wait for logon
if not client.wait_until_logged_on(timeout=10):
    error = client.last_logon_error()
    logger.error(f"❌ Logon failed: {error}")
    raise Exception(f"Logon failed: {error}")

logger.info("✅ Successfully logged on!")

# Wait for session to stabilize
time.sleep(1.0)

print("\n✅ Client ready for all examples!")
print("=" * 80)

[11:04:05] [INFO] 🔌 Connecting to PaperBroker...


📝 Configuration:
  username: BL01
  password: ***
  socket_host: 100.97.83.110
  socket_port: 5001
  sender_comp_id: BL-FIX
  target_comp_id: SERVER
  rest_base_url: http://100.97.83.110:9090
  account_d1: D1
  account_d2: D2
  symbol_derivative: HNXDS:VN30F2510

🔌 CREATING PERSISTENT CLIENT


[11:04:05] [INFO] ✅ Successfully logged on!



✅ Client ready for all examples!


---

## 2. Example 1: Simple Login & Account Info

**Goal:** Query account information using the connected client.

**What you'll learn:**
- Balance queries via REST API
- Using persistent connections
- Working with sub-accounts

In [3]:
print("=" * 80)
print("EXAMPLE 1: SIMPLE LOGIN & ACCOUNT INFO")
print("=" * 80)

logger.info("📊 Querying account information...")

# Query balances for both sub-accounts
with client.use_sub_account(CONFIG["account_d1"]):
    cash_d1 = client.get_cash_balance()
    total_d1 = client.get_account_balance()

with client.use_sub_account(CONFIG["account_d2"]):
    cash_d2 = client.get_cash_balance()
    total_d2 = client.get_account_balance()

logger.info("\n💰 Account D1:")
logger.info(f"   Available cash: {cash_d1.get('remainCash', 0):,.0f} VND")
logger.info(f"   Total balance: {total_d1.get('totalBalance', 0):,.0f} VND")

logger.info("\n💰 Account D2:")
logger.info(f"   Available cash: {cash_d2.get('remainCash', 0):,.0f} VND")
logger.info(f"   Total balance: {total_d2.get('totalBalance', 0):,.0f} VND")

print("\n✅ Example 1 completed!")
print("=" * 80)

[11:04:06] [INFO] 📊 Querying account information...
[11:04:06] [INFO] 
💰 Account D1:
[11:04:06] [INFO]    Available cash: 9,642,280,000 VND
[11:04:06] [INFO]    Total balance: 11,429,780,000 VND
[11:04:06] [INFO] 
💰 Account D2:
[11:04:06] [INFO]    Available cash: 9,642,280,000 VND
[11:04:06] [INFO]    Total balance: 8,569,780,000 VND


EXAMPLE 1: SIMPLE LOGIN & ACCOUNT INFO

✅ Example 1 completed!


---

## 3. Example 2: Order Cancellation

**Goal:** Place a limit order and cancel it before execution.

**What you'll learn:**
- Place limit orders
- Track order status with events
- Cancel pending orders

### Define Order Tracker

In [4]:
class OrderTracker:
    """Track order status and cancellation."""
    def __init__(self):
        self.order_accepted = ThreadEvent()
        self.order_canceled = ThreadEvent()
        self.order_id = None
        self.status = None
        
    def on_order_accepted(self, cl_ord_id, status, **kwargs):
        """Handle order accepted event."""
        if cl_ord_id == self.order_id:
            self.status = status
            logger.info(f"✅ Order accepted: {cl_ord_id[:8]}... (Status: {status})")
            self.order_accepted.set()
    
    def on_order_canceled(self, orig_cl_ord_id, status, **kwargs):
        """Handle order canceled event."""
        if orig_cl_ord_id == self.order_id:
            self.status = status
            logger.info(f"✅ Order canceled: {orig_cl_ord_id[:8]}... (Status: {status})")
            self.order_canceled.set()
    
    def on_order_rejected(self, cl_ord_id, reason, **kwargs):
        """Handle order rejected event."""
        if cl_ord_id == self.order_id:
            logger.error(f"❌ Order rejected: {cl_ord_id[:8]}... - {reason}")

print("✅ OrderTracker class defined")

✅ OrderTracker class defined


### Execute Cancellation

In [5]:
print("=" * 80)
print("EXAMPLE 2: ORDER CANCELLATION")
print("=" * 80)

# Configuration
symbol = CONFIG["symbol_derivative"]
price = 1250.0  # Unlikely to match
qty = 1
delay_seconds = 2

logger.info(f"Symbol: {symbol}")
logger.info(f"Account: {CONFIG['account_d1']}")
logger.info(f"Action: Place order → Wait {delay_seconds}s → Cancel")

# Initialize tracker
tracker = OrderTracker()

# Subscribe to events
client.on("fix:order:accepted", tracker.on_order_accepted)
client.on("fix:order:canceled", tracker.on_order_canceled)
client.on("fix:order:rejected", tracker.on_order_rejected)

# Place order using D1 sub-account
logger.info("\n📤 Placing SELL order...")
with client.use_sub_account(CONFIG["account_d1"]):
    order_id = client.place_order(
        full_symbol=symbol,
        side="SELL",
        qty=qty,
        price=price,
        ord_type="LIMIT"
    )

tracker.order_id = order_id
logger.info(f"Order ID: {order_id[:16]}...")

# Wait for acceptance
if not tracker.order_accepted.wait(timeout=10):
    logger.error("❌ Timeout waiting for order acceptance")
else:
    # Wait before canceling
    logger.info(f"\n⏳ Waiting {delay_seconds} seconds...")
    time.sleep(delay_seconds)
    
    # Cancel order
    logger.info(f"\n🗑️ Canceling order...")
    client.cancel_order(order_id)
    
    # Wait for cancellation
    if not tracker.order_canceled.wait(timeout=10):
        logger.warning("⚠️ Timeout waiting for cancellation")
    
    # Summary
    logger.info("\n📊 Summary:")
    logger.info(f"   Order ID: {order_id[:16]}...")
    logger.info(f"   Final Status: {tracker.status or 'UNKNOWN'}")
    logger.info(f"   Symbol: {symbol}")
    logger.info(f"   Quantity: {qty}")
    logger.info(f"   Price: {price:,.0f} VND")

print("\n✅ Example 2 completed!")
print("=" * 80)

[11:04:06] [INFO] Symbol: HNXDS:VN30F2510
[11:04:06] [INFO] Account: D1
[11:04:06] [INFO] Action: Place order → Wait 2s → Cancel
[11:04:06] [INFO] 
📤 Placing SELL order...
[11:04:06] [INFO] Order ID: da33bb21...
[11:04:06] [INFO] ✅ Order accepted: da33bb21... (Status: NEW)
[11:04:06] [INFO] 
⏳ Waiting 2 seconds...


EXAMPLE 2: ORDER CANCELLATION


[11:04:08] [INFO] 
🗑️ Canceling order...
[11:04:08] [INFO] ✅ Order canceled: da33bb21... (Status: CANCELED)
[11:04:08] [INFO] 
📊 Summary:
[11:04:08] [INFO]    Order ID: da33bb21...
[11:04:08] [INFO]    Final Status: CANCELED
[11:04:08] [INFO]    Symbol: HNXDS:VN30F2510
[11:04:08] [INFO]    Quantity: 1
[11:04:08] [INFO]    Price: 1,250 VND



✅ Example 2 completed!


---

## 4. Example 3: Cross-Matching Derivative

**Goal:** Demonstrate instant order matching between two sub-accounts.

**What you'll learn:**
- Multi-account trading (D1 ↔ D2)
- Cross-matching mechanism
- Event-driven fill tracking

### Define Cross-Match Tracker

In [6]:
class CrossMatchTracker:
    """Track cross-matching using events."""
    
    def __init__(self):
        self.orders = {}
        self.filled_event = ThreadEvent()
        self.fill_count = 0
    
    def on_order_filled(self, cl_ord_id, status, last_px, last_qty, **kw):
        """Event handler for filled orders."""
        logger.info(f"🔔 ORDER FILLED: {cl_ord_id[:8]}...")
        
        if cl_ord_id not in self.orders:
            self.orders[cl_ord_id] = {"status": status, "qty_filled": 0, "avg_price": 0}
        
        order = self.orders[cl_ord_id]
        order["status"] = status
        order["qty_filled"] = last_qty
        order["avg_price"] = last_px
        
        self.fill_count += 1
        logger.info(f"✅ Filled: {last_qty} @ {last_px:,.0f} VND")
        
        if self.fill_count >= 2:
            logger.info("🎯 Both orders filled - cross-match complete!")
            self.filled_event.set()
    
    def on_order_accepted(self, cl_ord_id, status, **kw):
        """Event handler for accepted orders."""
        logger.info(f"✓ Order ACCEPTED: {cl_ord_id[:8]}...")
    
    def on_order_rejected(self, cl_ord_id, reason, **kw):
        """Event handler for rejected orders."""
        logger.error(f"❌ Order REJECTED: {cl_ord_id[:8]}... | Reason: {reason}")

print("✅ CrossMatchTracker class defined")

✅ CrossMatchTracker class defined


### Execute Cross-Matching

In [7]:
print("=" * 80)
print("EXAMPLE 3: CROSS-MATCHING DERIVATIVE (D1 vs D2)")
print("=" * 80)

# Configuration
symbol = CONFIG["symbol_derivative"]
price = 1300.0
qty = 1

logger.info(f"Symbol: {symbol}")
logger.info(f"Sub-Accounts: {CONFIG['account_d1']} (seller) and {CONFIG['account_d2']} (buyer)")
logger.info("Mechanism: D2 can match unconditionally with D1")

# Initialize tracker
tracker_ex3 = CrossMatchTracker()

# Subscribe to events
client.on("fix:order:filled", tracker_ex3.on_order_filled)
client.on("fix:order:accepted", tracker_ex3.on_order_accepted)
client.on("fix:order:rejected", tracker_ex3.on_order_rejected)

# Show initial balances
with client.use_sub_account(CONFIG["account_d1"]):
    balance_d1 = client.get_cash_balance()
with client.use_sub_account(CONFIG["account_d2"]):
    balance_d2 = client.get_cash_balance()

logger.info("\n💰 Initial Balances:")
logger.info(f"   D1: {balance_d1.get('remainCash', 0):,.0f} VND")
logger.info(f"   D2: {balance_d2.get('remainCash', 0):,.0f} VND")

# Place orders
logger.info("\n📤 Placing Cross-Match Orders:")
logger.info(f"   Symbol: {symbol}")
logger.info(f"   Price: {price:,.0f}")
logger.info(f"   Quantity: {qty} contract(s)")
logger.info("\n   Strategy: D1 SELLS → D2 BUYS → INSTANT MATCH")

# D1 sells first
logger.info("\n   [1/2] D1 placing SELL order...")
with client.use_sub_account(CONFIG["account_d1"]):
    order_d1 = client.place_order(
        full_symbol=symbol,
        side="SELL",
        qty=qty,
        price=price,
        ord_type="LIMIT"
    )
logger.info(f"         Order ID: {order_d1[:8]}...")

time.sleep(1.0)  # Ensure D1 order is in book

# D2 buys (will match immediately)
logger.info("\n   [2/2] D2 placing BUY order...")
with client.use_sub_account(CONFIG["account_d2"]):
    order_d2 = client.place_order(
        full_symbol=symbol,
        side="BUY",
        qty=qty,
        price=price,
        ord_type="LIMIT"
    )
logger.info(f"         Order ID: {order_d2[:8]}...")

# Wait for fills
logger.info("\n⏳ Waiting for cross-match...")

if tracker_ex3.filled_event.wait(timeout=10):
    logger.info("\n🎉 CROSS-MATCH COMPLETED!")
    
    # Show results
    logger.info("\n📊 Trade Summary:")
    for cl_ord_id, order in tracker_ex3.orders.items():
        logger.info(
            f"   Order {cl_ord_id[:8]}... | "
            f"Status: {order['status']:8s} | "
            f"Filled: {order['qty_filled']} @ {order['avg_price']:,.0f} VND"
        )
    
    # Show updated balances
    with client.use_sub_account(CONFIG["account_d1"]):
        balance_d1_after = client.get_cash_balance()
    with client.use_sub_account(CONFIG["account_d2"]):
        balance_d2_after = client.get_cash_balance()
    
    logger.info("\n💰 Final Balances:")
    logger.info(f"   D1: {balance_d1_after.get('remainCash', 0):,.0f} VND")
    logger.info(f"   D2: {balance_d2_after.get('remainCash', 0):,.0f} VND")
else:
    logger.warning("\n⚠️ Timeout waiting for fills (10 seconds)")

print("\n✅ Example 3 completed!")
print("=" * 80)

[11:04:08] [INFO] Symbol: HNXDS:VN30F2510
[11:04:08] [INFO] Sub-Accounts: D1 (seller) and D2 (buyer)
[11:04:08] [INFO] Mechanism: D2 can match unconditionally with D1
[11:04:08] [INFO] 
💰 Initial Balances:
[11:04:08] [INFO]    D1: 9,642,280,000 VND
[11:04:08] [INFO]    D2: 9,642,280,000 VND
[11:04:08] [INFO] 
📤 Placing Cross-Match Orders:
[11:04:08] [INFO]    Symbol: HNXDS:VN30F2510
[11:04:08] [INFO]    Price: 1,300
[11:04:08] [INFO]    Quantity: 1 contract(s)
[11:04:08] [INFO] 
   Strategy: D1 SELLS → D2 BUYS → INSTANT MATCH
[11:04:08] [INFO] 
   [1/2] D1 placing SELL order...
[11:04:08] [INFO]          Order ID: 86379138...
[11:04:08] [INFO] ✓ Order ACCEPTED: 86379138...


EXAMPLE 3: CROSS-MATCHING DERIVATIVE (D1 vs D2)


[11:04:09] [INFO] 
   [2/2] D2 placing BUY order...
[11:04:09] [INFO]          Order ID: abe89c3b...
[11:04:09] [INFO] 
⏳ Waiting for cross-match...
[11:04:10] [INFO] ✓ Order ACCEPTED: abe89c3b...
[11:04:10] [INFO] 🔔 ORDER FILLED: abe89c3b...
[11:04:10] [INFO] ✅ Filled: 1.0 @ 1,300 VND
[11:04:10] [INFO] 🔔 ORDER FILLED: 86379138...
[11:04:10] [INFO] ✅ Filled: 1.0 @ 1,300 VND
[11:04:10] [INFO] 🎯 Both orders filled - cross-match complete!
[11:04:10] [INFO] 
🎉 CROSS-MATCH COMPLETED!
[11:04:10] [INFO] 
📊 Trade Summary:
[11:04:10] [INFO]    Order abe89c3b... | Status: FILLED   | Filled: 1.0 @ 1,300 VND
[11:04:10] [INFO]    Order 86379138... | Status: FILLED   | Filled: 1.0 @ 1,300 VND
[11:04:10] [INFO] 
💰 Final Balances:
[11:04:10] [INFO]    D1: 9,609,760,000 VND
[11:04:10] [INFO]    D2: 9,609,760,000 VND



✅ Example 3 completed!


---

## 5. Example 4: Advanced Cross-Matching

**Goal:** Demonstrate full fills vs multiple orders patterns.

**What you'll learn:**
- Full fill (1 order → 1 fill event)
- Multiple orders (3 orders → 3 fill events)
- FIFO matching at same price
- Detailed fill tracking

### Define Advanced Order Tracker

In [8]:
class D1OrderTracker:
    """Track D1 orders with focus on fill patterns."""
    
    def __init__(self):
        self.orders = {}  # {cl_ord_id: order_info}
        self.filled_event = ThreadEvent()
        self.target_orders = []  # D1 orders we're tracking
    
    def register_order(self, cl_ord_id, qty):
        """Register a D1 order for tracking."""
        self.orders[cl_ord_id] = {
            "status": "NEW",
            "qty_ordered": qty,
            "cum_qty": 0,
            "avg_price": 0,
            "fills": []
        }
        self.target_orders.append(cl_ord_id)
        logger.info(f"   📋 Registered: {cl_ord_id[:8]}... ({qty} contracts)")
    
    def on_order_filled(self, cl_ord_id, status, last_px, last_qty, cum_qty=None, **kw):
        """Handle fill events for D1 orders."""
        if cl_ord_id not in self.target_orders:
            return
        
        order = self.orders[cl_ord_id]
        order["status"] = status
        order["avg_price"] = last_px
        
        if cum_qty is not None:
            order["cum_qty"] = cum_qty
        else:
            order["cum_qty"] += last_qty
        
        fill_num = len(order["fills"]) + 1
        order["fills"].append({"fill_num": fill_num, "qty": last_qty, "price": last_px})
        
        is_fully_filled = order["cum_qty"] >= order["qty_ordered"]
        fill_type = "✅ FULL FILL" if is_fully_filled else "🔸 PARTIAL FILL"
        
        logger.info(
            f"      {fill_type} #{fill_num}: {last_qty} @ {last_px:,.0f} VND | "
            f"Progress: {order['cum_qty']}/{order['qty_ordered']}"
        )
        
        if self._all_orders_complete():
            self.filled_event.set()
    
    def _all_orders_complete(self):
        """Check if all D1 orders are fully filled."""
        for cl_ord_id in self.target_orders:
            order = self.orders[cl_ord_id]
            if order["cum_qty"] < order["qty_ordered"]:
                return False
        return True
    
    def on_order_accepted(self, cl_ord_id, status, **kw):
        if cl_ord_id in self.target_orders:
            logger.info(f"   ✓ Order accepted: {cl_ord_id[:8]}...")
    
    def on_order_rejected(self, cl_ord_id, reason, **kw):
        if cl_ord_id in self.target_orders:
            logger.error(f"   ✗ Order rejected: {cl_ord_id[:8]}... - {reason}")
    
    def print_summary(self):
        """Print detailed summary."""
        logger.info("\n📊 D1 ORDER EXECUTION SUMMARY")
        logger.info("=" * 80)
        
        total_orders = len(self.target_orders)
        total_fills = sum(len(self.orders[oid]["fills"]) for oid in self.target_orders)
        
        logger.info(f"Total D1 Orders: {total_orders}")
        logger.info(f"Total Fill Events: {total_fills}\n")
        
        for idx, cl_ord_id in enumerate(self.target_orders, 1):
            order = self.orders[cl_ord_id]
            logger.info(f"Order #{idx}: {cl_ord_id[:8]}...")
            logger.info(f"  Status: {order['status']}")
            logger.info(f"  Ordered: {order['qty_ordered']} contracts")
            logger.info(f"  Filled: {order['cum_qty']} contracts")
            logger.info(f"  Fills: {len(order['fills'])}")
            logger.info(f"  Avg Price: {order['avg_price']:,.0f} VND")
            
            if order['fills']:
                logger.info(f"  Fill History:")
                for fill in order['fills']:
                    logger.info(
                        f"    Fill #{fill['fill_num']}: "
                        f"{fill['qty']} @ {fill['price']:,.0f} VND"
                    )
            logger.info("")
        logger.info("=" * 80)

print("✅ D1OrderTracker class defined")

✅ D1OrderTracker class defined


### Scenario A: Full Fill

In [9]:
def run_scenario_a(tracker, symbol, price):
    """Scenario A: Full Fill (5 contracts → 1 fill event)."""
    logger.info("\n" + "🔷" * 40)
    logger.info("SCENARIO A: FULL FILL")
    logger.info("🔷" * 40)
    
    qty = 5
    
    logger.info(f"\n1️⃣ D1 places SELL: {qty} @ {price:,.0f}")
    with client.use_sub_account(CONFIG["account_d1"]):
        order_d1 = client.place_order(
            full_symbol=symbol, side="SELL", qty=qty, price=price, ord_type="LIMIT"
        )
    tracker.register_order(order_d1, qty)
    
    time.sleep(0.5)
    
    logger.info(f"\n2️⃣ D2 matches BUY: {qty} @ {price:,.0f}")
    with client.use_sub_account(CONFIG["account_d2"]):
        client.place_order(
            full_symbol=symbol, side="BUY", qty=qty, price=price, ord_type="LIMIT"
        )
    
    logger.info("\n⏳ Waiting for fill...")
    if tracker.filled_event.wait(timeout=5):
        logger.info("\n✅ Scenario A completed!")
        return True
    else:
        logger.warning("⚠️ Timeout!")
        return False

print("✅ Scenario A function defined")

✅ Scenario A function defined


### Scenario B: Multiple Orders

In [10]:
def run_scenario_b(tracker, symbol, price):
    """Scenario B: Multiple Orders (3 orders → 3 fill events)."""
    logger.info("\n" + "🔶" * 40)
    logger.info("SCENARIO B: MULTIPLE ORDERS")
    logger.info("🔶" * 40)
    
    orders = [
        {"qty": 2, "price": price},
        {"qty": 2, "price": price},
        {"qty": 1, "price": price},
    ]
    
    tracker.filled_event.clear()
    
    logger.info(f"\n1️⃣ D1 places {len(orders)} SELL orders:")
    d1_orders = []
    for i, spec in enumerate(orders, 1):
        qty = spec["qty"]
        px = spec["price"]
        logger.info(f"   Order {i}: {qty} @ {px:,.0f}")
        with client.use_sub_account(CONFIG["account_d1"]):
            order_id = client.place_order(
                full_symbol=symbol, side="SELL", qty=qty, price=px, ord_type="LIMIT"
            )
        tracker.register_order(order_id, qty)
        d1_orders.append((order_id, qty, px))
        time.sleep(0.5)
    
    time.sleep(1.0)
    
    logger.info("\n2️⃣ D2 matches each order:")
    for i, (order_id, qty, px) in enumerate(d1_orders, 1):
        logger.info(f"\n   Match {i}/{len(d1_orders)}: BUY {qty} @ {px:,.0f}")
        with client.use_sub_account(CONFIG["account_d2"]):
            client.place_order(
                full_symbol=symbol, side="BUY", qty=qty, price=px, ord_type="LIMIT"
            )
        time.sleep(0.8)
    
    logger.info("\n⏳ Waiting for all fills...")
    if tracker.filled_event.wait(timeout=15):
        logger.info("\n✅ Scenario B completed!")
        return True
    else:
        logger.warning("⚠️ Timeout!")
        return False

print("✅ Scenario B function defined")

✅ Scenario B function defined


### Execute Advanced Scenarios

In [11]:
print("=" * 80)
print("EXAMPLE 4: ADVANCED CROSS-MATCHING")
print("=" * 80)

symbol = CONFIG["symbol_derivative"]
price = 1300.0

logger.info(f"Symbol: {symbol}")
logger.info(f"Price: {price:,.0f}")
logger.info("Focus: Full fills vs Multiple orders")

# Initialize tracker
tracker_ex4 = D1OrderTracker()

# Subscribe to events
client.on("fix:order:filled", tracker_ex4.on_order_filled)
client.on("fix:order:accepted", tracker_ex4.on_order_accepted)
client.on("fix:order:rejected", tracker_ex4.on_order_rejected)

# Check balance
with client.use_sub_account(CONFIG["account_d1"]):
    balance = client.get_cash_balance()
logger.info(f"\n💰 D1 Balance: {balance.get('remainCash', 0):,.0f} VND\n")

# Run Scenario A
if not run_scenario_a(tracker_ex4, symbol, price):
    raise Exception("Scenario A failed")

time.sleep(2)

# Run Scenario B
if not run_scenario_b(tracker_ex4, symbol, price):
    raise Exception("Scenario B failed")

# Print summary
tracker_ex4.print_summary()

# Final balance
with client.use_sub_account(CONFIG["account_d1"]):
    balance_after = client.get_cash_balance()
logger.info(f"\n💰 D1 Final: {balance_after.get('remainCash', 0):,.0f} VND")

logger.info("\n🎉 ALL SCENARIOS COMPLETED!")
logger.info("\nKey Observations:")
logger.info("  • Scenario A: 1 order → 1 fill (full execution)")
logger.info("  • Scenario B: 3 orders → 3 fills (FIFO)")
logger.info("  • Same price → time-priority")
logger.info("  • Event-driven = real-time visibility")

print("\n✅ Example 4 completed!")
print("=" * 80)

[11:04:10] [INFO] Symbol: HNXDS:VN30F2510
[11:04:10] [INFO] Price: 1,300
[11:04:10] [INFO] Focus: Full fills vs Multiple orders
[11:04:10] [INFO] 
💰 D1 Balance: 9,609,760,000 VND

[11:04:10] [INFO] 
🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷
[11:04:10] [INFO] SCENARIO A: FULL FILL
[11:04:10] [INFO] 🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷🔷
[11:04:10] [INFO] 
1️⃣ D1 places SELL: 5 @ 1,300
[11:04:10] [INFO]    📋 Registered: 9513bb43... (5 contracts)
[11:04:10] [INFO] ✓ Order ACCEPTED: 9513bb43...
[11:04:10] [INFO]    ✓ Order accepted: 9513bb43...


EXAMPLE 4: ADVANCED CROSS-MATCHING


[11:04:10] [INFO] 
2️⃣ D2 matches BUY: 5 @ 1,300
[11:04:10] [INFO] 
⏳ Waiting for fill...
[11:04:10] [INFO] ✓ Order ACCEPTED: 878ddd5f...
[11:04:10] [INFO] 🔔 ORDER FILLED: 878ddd5f...
[11:04:10] [INFO] ✅ Filled: 5.0 @ 1,300 VND
[11:04:10] [INFO] 🎯 Both orders filled - cross-match complete!
[11:04:10] [INFO] 🔔 ORDER FILLED: 9513bb43...
[11:04:10] [INFO] ✅ Filled: 5.0 @ 1,300 VND
[11:04:10] [INFO] 🎯 Both orders filled - cross-match complete!
[11:04:10] [INFO]       ✅ FULL FILL #1: 5.0 @ 1,300 VND | Progress: 5.0/5
[11:04:10] [INFO] 
✅ Scenario A completed!
[11:04:12] [INFO] 
🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶
[11:04:12] [INFO] SCENARIO B: MULTIPLE ORDERS
[11:04:12] [INFO] 🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶🔶
[11:04:12] [INFO] 
1️⃣ D1 places 3 SELL orders:
[11:04:12] [INFO]    Order 1: 2 @ 1,300
[11:04:12] [INFO]    📋 Registered: 55625562... (2 contracts)
[11:04:12] [INFO] ✓ Order ACCEPTED: 55625562...
[11:04:12] [INFO]    ✓ Order accepted: 55625562...
[11:04:13] [INFO]    Order


✅ Example 4 completed!


---

## 6. Summary & Best Practices

### 🎓 What You Learned

1. **Single Persistent Connection**
   - One client for all examples
   - No disconnect/reconnect overhead
   - More efficient resource usage

2. **Sub-Account Management**
   - Use `client.use_sub_account(id)` context manager
   - Thread-safe switching
   - Clean and elegant code

3. **Event-Driven Architecture**
   - No polling loops
   - Instant notifications
   - Low CPU usage

4. **Order Management**
   - Place limit orders
   - Cancel pending orders
   - Track order status in real-time

5. **Cross-Matching**
   - Multi-account trading (D1 ↔ D2)
   - Instant unconditional matching
   - Full fills vs multiple orders

---

### ✅ Best Practices

#### 1. Always Use Context Manager for Sub-Accounts
```python
# ✅ Good: Clear scope
with client.use_sub_account('D1'):
    client.place_order(...)

# ❌ Bad: No explicit scope
client.set_default_sub_account('D1')
client.place_order(...)
```

#### 2. Always Use Event Handlers
```python
# ❌ Bad: Polling
while not order_filled:
    time.sleep(0.01)
    check_status()

# ✅ Good: Events
def on_fill(order_id, **kw):
    print(f"Filled: {order_id}")

client.on("fix:order:filled", on_fill)
```

#### 3. Include **kwargs in Handlers
```python
# ✅ Always include **kwargs for future compatibility
def on_event(required_param, **kwargs):
    pass
```

#### 4. Handle Errors Gracefully
```python
if not client.wait_until_logged_on(timeout=10):
    error = client.last_logon_error()
    logger.error(f"Failed: {error}")
    return
```

#### 5. Set console=False for Production
```python
# Only show WARNING/ERROR in console
# DEBUG/INFO goes to log file
client = PaperBrokerClient(..., console=False)
```

---

### 📚 Next Steps

1. **Read Core Guides**
   - Event System Guide - Deep dive into events
   - Configuration Guide - Advanced config
   - Market Data Guide - Real-time quotes

2. **Try More Examples**
   - OHLC calculator
   - Complete trading bot

3. **Build Your Strategy**
   - Use event-driven approach
   - Integrate market data
   - Test with paper trading

---

### 🎉 Congratulations!

You've completed the **PaperBroker Client Tutorial**!

**You now know how to:**
- ✅ Connect to PaperBroker with persistent connection
- ✅ Use sub-account context manager
- ✅ Place and cancel orders
- ✅ Use event-driven architecture
- ✅ Manage multiple accounts
- ✅ Track order fills in real-time

**Ready to build amazing trading strategies!** 🚀📈

---

*Happy Trading!* 🎯

---

## 7. Cleanup (Optional)

Run this cell when you're completely done to disconnect the client.

**Note:** Throughout the tutorial, we kept the connection alive for efficiency. Only disconnect when you're done with ALL trading activities.

In [12]:
print("=" * 80)
print("🔌 DISCONNECTING CLIENT")
print("=" * 80)

logger.info("Disconnecting...")
# Note: client.disconnect() may cause issues with QuickFIX cleanup
# In production, you might want to use os._exit(0) or let the process end naturally

logger.info("✅ Session ended")
print("=" * 80)

[11:04:19] [INFO] Disconnecting...
[11:04:19] [INFO] ✅ Session ended


🔌 DISCONNECTING CLIENT
